# PART 1

The gravity assist was successful, and you're well on your way to the Venus refuelling station. During the rush back on Earth, the fuel management system wasn't completely installed, so that's next on the priority list.

Opening the front panel reveals a jumble of wires. Specifically, two wires are connected to a central port and extend outward on a grid. You trace the path each wire takes as it leaves the central port, one wire per line of text (your puzzle input).

The wires twist and turn, but the two wires occasionally cross paths. To fix the circuit, you need to find the intersection point closest to the central port. Because the wires are on a grid, use the Manhattan distance for this measurement. While the wires do technically cross right at the central port where they both start, this point does not count, nor does a wire count as crossing with itself.

For example, if the first wire's path is R8,U5,L5,D3, then starting from the central port (o), it goes right 8, up 5, left 5, and finally down 3:

In [2]:
#...........
#...........
#...........
#....+----+.
#....|....|.
#....|....|.
#....|....|.
#.........|.
#.o-------+.
#...........

Then, if the second wire's path is U7,R6,D4,L4, it goes up 7, right 6, down 4, and left 4:

In [ ]:
#...........
#.+-----+...
#.|.....|...
#.|..+--X-+.
#.|..|..|.|.
#.|.-X--+.|.
#.|..|....|.
#.|.......|.
#.o-------+.
#...........

These wires cross at two locations (marked X), but the lower-left one is closer to the central port: its distance is 3 + 3 = 6.

Here are a few more examples:

    -  R75,D30,R83,U83,L12,D49,R71,U7,L72
U62,R66,U55,R34,D71,R55,D58,R83 = distance 159

- R98,U47,R26,D63,R33,U87,L62,D20,R33,U53,R51
U98,R91,D20,R16,D67,R40,U7,R15,U6,R7 = distance 135
What is the Manhattan distance from the central port to the closest intersection?

In [186]:
# dependencies
import os
import csv
import time
import pickle
from datetime import datetime, timedelta

# data science
import numpy as np
import pandas as pd

# web scraping
import requests
import urllib.request
from bs4 import BeautifulSoup as bs

In [187]:
# df = pd.read_csv('data.csv', header=None)

#### DATA

In [188]:
wire1 = open('wire1.txt', 'r').readlines()
wire1 = wire1[0].split(",")
print(wire1)

['R992', 'U221', 'L822', 'U805', 'R667', 'D397', 'L969', 'U433', 'R918', 'D517', 'L494', 'U909', 'L224', 'D738', 'R247', 'D312', 'L803', 'D656', 'L571', 'D968', 'L392', 'D332', 'L581', 'U487', 'R522', 'D780', 'L74', 'D561', 'L246', 'U380', 'L125', 'U11', 'R735', 'D761', 'R482', 'D208', 'R985', 'D991', 'L352', 'U140', 'L586', 'D492', 'L777', 'U96', 'R682', 'D969', 'R775', 'U279', 'R671', 'D423', 'R838', 'U907', 'L486', 'D702', 'L432', 'D625', 'R463', 'U559', 'R12', 'D531', 'R510', 'D347', 'R147', 'U949', 'R175', 'U160', 'L975', 'D627', 'L537', 'D343', 'L406', 'D237', 'R953', 'U725', 'L996', 'D740', 'L703', 'D996', 'R157', 'U356', 'R247', 'D541', 'L592', 'D345', 'R580', 'U656', 'R50', 'D423', 'L158', 'U502', 'L86', 'U729', 'L720', 'D464', 'R901', 'D739', 'L20', 'U21', 'R497', 'D14', 'L580', 'U610', 'L114', 'D858', 'R853', 'U550', 'L354', 'D433', 'L507', 'U144', 'R9', 'U422', 'R674', 'U604', 'R107', 'D999', 'L420', 'U675', 'R538', 'D491', 'R84', 'D158', 'R303', 'D450', 'L616', 'U938', 'L1

In [189]:
wire2 = open('wire2.txt', 'r').readlines()
wire2 = wire2[0].split(",")
print(wire2)

['L998', 'U308', 'R889', 'D471', 'R719', 'U326', 'L6', 'U802', 'L608', 'U149', 'R454', 'U6', 'R837', 'U255', 'L720', 'D60', 'L426', 'D525', 'L190', 'U995', 'R676', 'U172', 'R910', 'U645', 'R249', 'D725', 'R355', 'U668', 'L988', 'U253', 'L820', 'D266', 'R836', 'D750', 'R998', 'U113', 'L502', 'U634', 'L620', 'U903', 'L542', 'D426', 'L497', 'D766', 'R930', 'U415', 'R655', 'D676', 'L694', 'D548', 'L280', 'U895', 'L899', 'U235', 'R912', 'D257', 'R161', 'D834', 'R88', 'D379', 'L723', 'U508', 'L604', 'D1', 'R706', 'D321', 'R725', 'U986', 'R52', 'D741', 'L738', 'D810', 'R595', 'U352', 'L835', 'D712', 'R797', 'D332', 'L451', 'D145', 'L608', 'U940', 'R886', 'D945', 'R929', 'D4', 'R332', 'D303', 'L877', 'D927', 'R686', 'U762', 'L588', 'D496', 'R352', 'D516', 'R355', 'D299', 'L459', 'D831', 'R9', 'U322', 'R635', 'U895', 'L127', 'U27', 'R996', 'D491', 'L360', 'U921', 'L146', 'U833', 'L420', 'D60', 'R32', 'D936', 'R815', 'D451', 'R715', 'U570', 'R889', 'D35', 'R135', 'U814', 'L559', 'D141', 'L470', 

#### METHODS & TESTS

In [190]:
def coordinator(coordinate):
    direction = coordinate[0]
    distance = int(coordinate[1:])
    return direction, distance

In [212]:
# # check distance
# for turn in wire:
#         d1, d2 = coordinator(turn)

In [218]:
def matrix(x,y, d1, d2, coordinates):
    for i in np.arange(d2):
        if d1 == 'L':
            x = x-1
        elif d1 == 'R':
            x = x+1
        elif d1 == 'U':
            y = y+1
        else:
            y = y-1
        coord = (x,y)
        coordinates.append(coord)
    return coordinates, x, y, d2

In [219]:
# TEST
d1, d2 = coordinator(wire1[0])
print(d1)
print(type(d1))
print(d2)
print(type(d2))

R
<class 'str'>
992
<class 'int'>


In [220]:
# initialize at the central port
x = 0
y = 0
coordinates = []

In [221]:
coordinates, x, y, distance = matrix(x,y,d1,d2,coordinates)

In [222]:
print(coordinates)
print(x)
print(y)
print(distance)

[(1, 0), (2, 0), (3, 0), (4, 0), (5, 0), (6, 0), (7, 0), (8, 0), (9, 0), (10, 0), (11, 0), (12, 0), (13, 0), (14, 0), (15, 0), (16, 0), (17, 0), (18, 0), (19, 0), (20, 0), (21, 0), (22, 0), (23, 0), (24, 0), (25, 0), (26, 0), (27, 0), (28, 0), (29, 0), (30, 0), (31, 0), (32, 0), (33, 0), (34, 0), (35, 0), (36, 0), (37, 0), (38, 0), (39, 0), (40, 0), (41, 0), (42, 0), (43, 0), (44, 0), (45, 0), (46, 0), (47, 0), (48, 0), (49, 0), (50, 0), (51, 0), (52, 0), (53, 0), (54, 0), (55, 0), (56, 0), (57, 0), (58, 0), (59, 0), (60, 0), (61, 0), (62, 0), (63, 0), (64, 0), (65, 0), (66, 0), (67, 0), (68, 0), (69, 0), (70, 0), (71, 0), (72, 0), (73, 0), (74, 0), (75, 0), (76, 0), (77, 0), (78, 0), (79, 0), (80, 0), (81, 0), (82, 0), (83, 0), (84, 0), (85, 0), (86, 0), (87, 0), (88, 0), (89, 0), (90, 0), (91, 0), (92, 0), (93, 0), (94, 0), (95, 0), (96, 0), (97, 0), (98, 0), (99, 0), (100, 0), (101, 0), (102, 0), (103, 0), (104, 0), (105, 0), (106, 0), (107, 0), (108, 0), (109, 0), (110, 0), (111, 0

#### LOOPY MAGOO

In [209]:
def wirecutter(wire):
    x = 0
    y = 0
    distance = 0
    coordinates = []
    for turn in wire:
        d1, d2 = coordinator(turn)
        coordinates, x, y, d = matrix(x, y, d1, d2, coordinates)
        distance = distance + d
    return coordinates, distance

In [224]:
wire1_coords, wire1_dist = wirecutter(wire1)
print(wire1_coords)
print(wire1_dist)

[(1, 0), (2, 0), (3, 0), (4, 0), (5, 0), (6, 0), (7, 0), (8, 0), (9, 0), (10, 0), (11, 0), (12, 0), (13, 0), (14, 0), (15, 0), (16, 0), (17, 0), (18, 0), (19, 0), (20, 0), (21, 0), (22, 0), (23, 0), (24, 0), (25, 0), (26, 0), (27, 0), (28, 0), (29, 0), (30, 0), (31, 0), (32, 0), (33, 0), (34, 0), (35, 0), (36, 0), (37, 0), (38, 0), (39, 0), (40, 0), (41, 0), (42, 0), (43, 0), (44, 0), (45, 0), (46, 0), (47, 0), (48, 0), (49, 0), (50, 0), (51, 0), (52, 0), (53, 0), (54, 0), (55, 0), (56, 0), (57, 0), (58, 0), (59, 0), (60, 0), (61, 0), (62, 0), (63, 0), (64, 0), (65, 0), (66, 0), (67, 0), (68, 0), (69, 0), (70, 0), (71, 0), (72, 0), (73, 0), (74, 0), (75, 0), (76, 0), (77, 0), (78, 0), (79, 0), (80, 0), (81, 0), (82, 0), (83, 0), (84, 0), (85, 0), (86, 0), (87, 0), (88, 0), (89, 0), (90, 0), (91, 0), (92, 0), (93, 0), (94, 0), (95, 0), (96, 0), (97, 0), (98, 0), (99, 0), (100, 0), (101, 0), (102, 0), (103, 0), (104, 0), (105, 0), (106, 0), (107, 0), (108, 0), (109, 0), (110, 0), (111, 0

In [225]:
wire2_coords, wire2_dist = wirecutter(wire2)
print(wire2_coords)
print(wire2_dist)

[(-1, 0), (-2, 0), (-3, 0), (-4, 0), (-5, 0), (-6, 0), (-7, 0), (-8, 0), (-9, 0), (-10, 0), (-11, 0), (-12, 0), (-13, 0), (-14, 0), (-15, 0), (-16, 0), (-17, 0), (-18, 0), (-19, 0), (-20, 0), (-21, 0), (-22, 0), (-23, 0), (-24, 0), (-25, 0), (-26, 0), (-27, 0), (-28, 0), (-29, 0), (-30, 0), (-31, 0), (-32, 0), (-33, 0), (-34, 0), (-35, 0), (-36, 0), (-37, 0), (-38, 0), (-39, 0), (-40, 0), (-41, 0), (-42, 0), (-43, 0), (-44, 0), (-45, 0), (-46, 0), (-47, 0), (-48, 0), (-49, 0), (-50, 0), (-51, 0), (-52, 0), (-53, 0), (-54, 0), (-55, 0), (-56, 0), (-57, 0), (-58, 0), (-59, 0), (-60, 0), (-61, 0), (-62, 0), (-63, 0), (-64, 0), (-65, 0), (-66, 0), (-67, 0), (-68, 0), (-69, 0), (-70, 0), (-71, 0), (-72, 0), (-73, 0), (-74, 0), (-75, 0), (-76, 0), (-77, 0), (-78, 0), (-79, 0), (-80, 0), (-81, 0), (-82, 0), (-83, 0), (-84, 0), (-85, 0), (-86, 0), (-87, 0), (-88, 0), (-89, 0), (-90, 0), (-91, 0), (-92, 0), (-93, 0), (-94, 0), (-95, 0), (-96, 0), (-97, 0), (-98, 0), (-99, 0), (-100, 0), (-101, 

In [226]:
def intersector(a,b):
    intersection = []
    intersection_set = set(a).intersection(b)
    for intersect in intersection_set:
        intersection.append(intersect)
    return intersection

In [227]:
intersection = intersector(wire1_coords,wire2_coords)
print(intersection)

[(681, 545), (604, 221), (297, 1026), (68, 815), (170, 815), (-49, 1062), (57, 404), (403, 0), (-488, 0), (837, 712), (68, 1064), (292, 965), (292, 815), (57, 1062), (604, 545), (156, 1454), (292, 1315), (258, 1454), (-4, 1062), (-488, 308), (170, 965), (681, 0), (292, 1064), (68, 965), (604, 629), (610, 0), (292, 1114), (68, 790), (292, 1091), (854, 221), (315, 712), (786, 712), (57, 629), (297, 1062), (297, 716), (292, 1277), (681, 629), (141, 1062), (68, 1114), (-132, 815), (681, 221), (170, 352), (-205, 404)]


In [228]:
def manhattan(intersection):
    length_list = []
    cp = (0,0)
    for ray in intersection:
        length_list.append(abs(cp[0]-ray[0])+abs(cp[1]-ray[1]))
    return length_list

In [229]:
manhattan_distances = manhattan(intersection)
print(manhattan_distances)

[1226, 825, 1323, 883, 985, 1111, 461, 403, 488, 1549, 1132, 1257, 1107, 1119, 1149, 1610, 1607, 1712, 1066, 796, 1135, 681, 1356, 1033, 1233, 610, 1406, 858, 1383, 1075, 1027, 1498, 686, 1359, 1013, 1569, 1310, 1203, 1182, 947, 902, 522, 609]


In [230]:
min(manhattan_distances)

403

#### TESTER

In [161]:
wirea = ['R75','D30','R83','U83','L12','D49','R71','U7','L72']
wireb = ['U62','R66','U55','R34','D71','R55','D58','R83']

In [162]:
testa = wirecutter(wirea)
testb = wirecutter(wireb)

In [163]:
test_intersection = intersector(testa, testb)
print(test_intersection)

[(158, -12), (146, 46), (155, 4), (155, 11)]


In [164]:
test_distances = manhattan(test_intersection)
print(test_distances)

[170, 192, 159, 166]


In [165]:
min(test_distances)

159

In [166]:
wirec = ['R75','D30','R83','U83','L12','D49','R71','U7','L72','U62','R66','U55','R34','D71','R55','D58','R83']
wired = ['R98','U47','R26','D63','R33','U87','L62','D20','R33','U53','R51','U98','R91','D20','R16',D67,R40,U7,R15,U6,R7]

In [167]:
testc = wirecutter(wirec)
testd = wirecutter(wired)

In [168]:
test_intersection_2 = intersector(testc, testd)
print(test_intersection_2)

[(107, 71), (157, 18), (124, 11), (107, 47), (107, 51)]


In [169]:
test_distances_2 = manhattan(test_intersection_2)
print(test_distances_2)

[178, 175, 135, 154, 158]


In [170]:
min(test_distances_2)

135

# PART 2
What is the fewest combined steps the wires must take to reach an intersection?

In [235]:
steplist = []
for c in intersection:
    i1 = wire1_coords.index(c)+1    
    i2 = wire2_coords.index(c)+1
    steplist.append(i1+i2)

In [236]:
min(steplist)

4158